In [11]:
import pandas as pd
import numpy as np

In [2]:
t = pd.read_csv('train.csv')
train = t['Title']
label_train = t['Class Index']
label_train = [i-1 for i in label_train]

t = pd.read_csv('test.csv')
test = t['Title']
label_test = t['Class Index']
label_test = [i-1 for i in label_test]

In [3]:
import nltk
from nltk.corpus import stopwords

corpus_train = []
corpus_test = []
punc = '''()-[]{};:'"\,<>/@#$%^&*_.~”'''
stop = set(stopwords.words('english'))

for i in train:
    tokens = nltk.word_tokenize(i)
    tokens = [w for w in tokens if w not in punc]
    tokens = [w for w in tokens if w not in stop]
    corpus_train.append(tokens)

for i in test:
    tokens = nltk.word_tokenize(i)
    tokens = [w for w in tokens if w not in punc]
    tokens = [w for w in tokens if w not in stop]
    corpus_test.append(tokens)

['Wall', 'St.', 'Bears', 'Claw', 'Back', 'Into', 'Black', 'Reuters']
['Carlyle', 'Looks', 'Toward', 'Commercial', 'Aerospace', 'Reuters']
['Oil', 'Economy', 'Cloud', 'Stocks', 'Outlook', 'Reuters']
['Iraq', 'Halts', 'Oil', 'Exports', 'Main', 'Southern', 'Pipeline', 'Reuters']
['Oil', 'prices', 'soar', 'all-time', 'record', 'posing', 'new', 'menace', 'US', 'economy', 'AFP']
['Stocks', 'End', 'Up', 'But', 'Near', 'Year', 'Lows', 'Reuters']
['Money', 'Funds', 'Fell', 'Latest', 'Week', 'AP']
['Fed', 'minutes', 'show', 'dissent', 'inflation', 'USATODAY.com']
['Safety', 'Net', 'Forbes.com']
['Wall', 'St.', 'Bears', 'Claw', 'Back', 'Into', 'Black']
['Oil', 'Economy', 'Cloud', 'Stocks', 'Outlook']
['No', 'Need', 'OPEC', 'Pump', 'More-Iran', 'Gov']
['Non-OPEC', 'Nations', 'Should', 'Up', 'Output-Purnomo']
['Google', 'IPO', 'Auction', 'Off', 'Rocky', 'Start']
['Dollar', 'Falls', 'Broadly', 'Record', 'Trade', 'Gap']
['Rescuing', 'Old', 'Saver']
['Kids', 'Rule', 'Back-to-School']
['In', 'Down', 'M

In [7]:
from gensim.models import word2vec
from gensim.models.word2vec import Word2Vec

model = Word2Vec.load('20200219-wiki-word2vec/wiki-lemma-100D-phrase')

train_max = 0
test_max = 0
max_len = 0

for i in corpus_train:
    if len(i) > train_max:
        train_max = len(i)
        
for i in corpus_test:
    if len(i) > test_max:
        test_max = len(i)
        
if train_max > test_max:
    max_len = train_max
else:
    max_len = test_max
    
feature = []
t_feature = []

# size of corpus_train matrix of each corpus: max_len*100
for i in range(len(corpus_train)):
    vec = np.zeros((max_len, 100))
    
    for j in range(len(corpus_train[i])):
        if corpus_train[i][j] in model.wv.key_to_index:
            vec[j] = model.wv[corpus_train[i][j]]
        else:
            vec[j] = np.zeros(100)

    feature.append(vec)
    
for i in range(len(corpus_test)):
    vec = np.zeros((max_len, 100))
    
    for j in range(len(corpus_test[i])):
        if corpus_test[i][j] in model.wv.key_to_index:
            vec[j] = model.wv[corpus_test[i][j]]
        else:
            vec[j] = np.zeros(100)

    t_feature.append(vec)

feature = np.array(feature)
t_feature = np.array(t_feature)
feature = feature.reshape(feature.shape[0], (feature.shape[1]*feature.shape[2]))
t_feature = t_feature.reshape(t_feature.shape[0], (t_feature.shape[1]*t_feature.shape[2]))

In [8]:
# train and validate
from sklearn.model_selection import train_test_split
from sklearn import ensemble
from sklearn.metrics import classification_report

f_train, f_val, l_train, l_val = train_test_split(feature, label_train, test_size=0.3)

model = ensemble.RandomForestClassifier()
model.fit(f_train, l_train)
predict_val = model.predict(f_val)
print(classification_report(predict_val, l_val))

              precision    recall  f1-score   support

           0       0.82      0.80      0.81      9371
           1       0.87      0.79      0.83      9870
           2       0.70      0.79      0.75      8051
           3       0.75      0.77      0.76      8708

    accuracy                           0.79     36000
   macro avg       0.79      0.79      0.79     36000
weighted avg       0.79      0.79      0.79     36000



In [10]:
# test
predict_test = model.predict(t_feature)
print(classification_report(predict_test, label_test))

              precision    recall  f1-score   support

           0       0.82      0.77      0.79      2019
           1       0.87      0.80      0.84      2066
           2       0.68      0.78      0.73      1665
           3       0.75      0.77      0.76      1850

    accuracy                           0.78      7600
   macro avg       0.78      0.78      0.78      7600
weighted avg       0.79      0.78      0.78      7600

